In [1]:
import json
import pandas as pd

# Load the data from the enterprise-attack.json file
with open('../data/enterprise-attack.json') as f:
    enterprise_attack = json.load(f)

# # Load the data from the nist_800_53-rev5_attack-14.1-enterprise_json.json file
# with open('../data/nist_800_53-rev5_attack-14.1-enterprise_json.json') as f:
#     nist_mapping = json.load(f)

# Extract ATT&CK groups
attack_groups = []

for obj in enterprise_attack['objects']:
    if obj['type'] == 'intrusion-set':
        attack_groups.append({
            "name": obj.get('name', 'N/A'),
            "description": obj.get('description', 'N/A')
        })

# Create a DataFrame to display the information
attack_groups_df = pd.DataFrame(attack_groups)
attack_groups_df.head()  # display the first few rows to ensure it's correctly formatted

name                                        description
0  Indrik Spider  [Indrik Spider](https://attack.mitre.org/group...
1   LuminousMoth  [LuminousMoth](https://attack.mitre.org/groups...
2  Wizard Spider  [Wizard Spider](https://attack.mitre.org/group...
3      Elderwood  [Elderwood](https://attack.mitre.org/groups/G0...
4   Frankenstein  [Frankenstein](https://attack.mitre.org/groups...

In [2]:
# Define keywords indicative of the retail industry
keywords = ["retail", "merchant", "shopper", "store", "point of sale", "POS", "e-commerce"]

# Filter groups based on the given keywords in their descriptions
retail_related_groups = []

for obj in enterprise_attack['objects']:
    if obj['type'] == 'intrusion-set':
        description = obj.get('description', '').lower()
        if any(keyword in description for keyword in keywords):
            retail_related_groups.append({
                "name": obj.get('name', 'N/A'),
                "description": obj.get('description', 'N/A')
            })

# Create a DataFrame to display the filtered information
retail_related_groups_df = pd.DataFrame(retail_related_groups)
retail_related_groups_df

name                                        description
0              FIN7  [FIN7](https://attack.mitre.org/groups/G0046) ...
1              FIN6  [FIN6](https://attack.mitre.org/groups/G0037) ...
2             FIN13  [FIN13](https://attack.mitre.org/groups/G1016)...
3              FIN8  [FIN8](https://attack.mitre.org/groups/G0061) ...
4  Scattered Spider  [Scattered Spider](https://attack.mitre.org/gr...

In [3]:
############################################################

In [4]:
# Identify FIN7's intrusion set ID and gather relevant relationships
fin7_id = None
fin7_relationships = []

# First, find the FIN7 intrusion set ID
for obj in enterprise_attack['objects']:
    if obj['type'] == 'intrusion-set' and 'FIN7' in obj.get('name', ''):
        fin7_id = obj['id']
        break

# Next, gather all relationship objects relevant to FIN7's intrusion set ID
if fin7_id:
    for obj in enterprise_attack['objects']:
        if obj['type'] == 'relationship' and obj['source_ref'] == fin7_id:
            fin7_relationships.append(obj)

fin7_id, len(fin7_relationships)  # Display the FIN7 ID and count of related relationships

('intrusion-set--3753cc21-2dae-4dfb-8481-d004e74502cc', 70)

In [5]:
# Manually inspect a small subset of data to locate FIN7 techniques
import itertools

# Establish keywords to identify FIN7 related objects
fin7_name = 'FIN7'

# Extract top few objects for manual processing
subset_objects = list(itertools.islice((obj for obj in enterprise_attack['objects'] if obj['type'] == 'relationship' or obj['type'] == 'intrusion-set'), 100))

# Create a dictionary to store results
inspection_results = {
    "intrusion-sets": [],
    "relationships": [],
    "attack-patterns": []
}

# Manual inspection function
def manual_inspection(obj_list, ids_to_check):
    extracted_info = []
    for obj in obj_list:
        if obj['id'] in ids_to_check:
            extracted_info.append(obj)
    return extracted_info

# Step 1: Identify the intrusion set ID for FIN7
for obj in subset_objects:
    if obj['type'] == 'intrusion-set' and 'FIN7' in obj.get('name', ''):
        inspection_results['intrusion-sets'].append(obj)
        fin7_id = obj['id']
        break

# Step 2: Gather relationships related to FIN7
if fin7_id:
    for obj in subset_objects:
        if obj['type'] == 'relationship' and obj['source_ref'] == fin7_id:
            inspection_results['relationships'].append(obj)

# Step 3: Identify relevant attack patterns and tools
relationship_ids = [r['target_ref'] for r in inspection_results['relationships']]
inspection_results['attack-patterns'] = manual_inspection(subset_objects, relationship_ids)

inspection_results

{'intrusion-sets': [],
 'relationships': [{'object_marking_refs': ['marking-definition--fa42a846-8d90-4e51-bc29-71d5b4802168'],
   'id': 'relationship--00561c3c-345e-4578-95c3-b7e0a95db7b1',
   'type': 'relationship',
   'created': '2021-09-22T14:33:04.183Z',
   'created_by_ref': 'identity--c78cb6e5-0c4b-4611-8297-d1b8b55e40b5',
   'external_references': [{'source_name': 'CrowdStrike Carbon Spider August 2021',
     'url': 'https://www.crowdstrike.com/blog/carbon-spider-embraces-big-game-hunting-part-1/',
     'description': 'Loui, E. and Reynolds, J. (2021, August 30). CARBON SPIDER Embraces Big Game Hunting, Part 1. Retrieved September 20, 2021.'}],
   'modified': '2021-09-22T14:33:04.183Z',
   'description': '[FIN7](https://attack.mitre.org/groups/G0046) has used malicious links to lure victims into downloading malware.(Citation: CrowdStrike Carbon Spider August 2021)',
   'relationship_type': 'uses',
   'source_ref': 'intrusion-set--3753cc21-2dae-4dfb-8481-d004e74502cc',
   'target

In [6]:
############################################################    

In [7]:
# Manually extract TTPs and Tools for FIN7 from ATT&CK framework with adjusted approach to avoid internal exceptions.
# Let's focus first on extracting techniques related to FIN7

# List to store techniques related to FIN7
fin7_techniques = []

# Extract techniques associated with FIN7 from relationships
for obj in enterprise_attack['objects']:
    if obj['type'] == 'relationship' and obj.get('source_ref') == fin7_id and obj['relationship_type'] == 'uses':
        target_ref = obj.get('target_ref')
        target_obj = next((item for item in enterprise_attack['objects'] if item['id'] == target_ref), None)
        if target_obj and target_obj['type'] == 'attack-pattern':
            fin7_techniques.append(target_obj)

# Create a structured table with technique information
techniques_info = []
for tech in fin7_techniques:
    tech_info = {
        "Technique ID": tech['external_references'][0].get('external_id', 'N/A'),
        "Technique Name": tech.get('name', 'N/A'),
        "Description": tech.get('description', 'N/A'),
        "Tactic": tech.get('kill_chain_phases', [{'phase_name': 'N/A'}])[0].get('phase_name', 'N/A')
    }
    techniques_info.append(tech_info)

# Convert to DataFrame for display
fin7_techniques_df = pd.DataFrame(techniques_info)
fin7_techniques_df.head()  # display first few techniques to ensure correct formatting

Technique ID                     Technique Name  \
0    T1204.001                     Malicious Link   
1    T1553.002                       Code Signing   
2        T1078                     Valid Accounts   
3        T1059  Command and Scripting Interpreter   
4    T1021.004                                SSH   

                                         Description            Tactic  
0  An adversary may rely upon a user clicking a m...         execution  
1  Adversaries may create, acquire, or steal code...   defense-evasion  
2  Adversaries may obtain and abuse credentials o...   defense-evasion  
3  Adversaries may abuse command and script inter...         execution  
4  Adversaries may use [Valid Accounts](https://a...  lateral-movement

In [8]:
# Define helper functions to extract related objects from MITRE dataset
def get_intrusion_set_id(group_name, attack_objects):
    for obj in attack_objects:
        if obj['type'] == 'intrusion-set' and obj.get('name') == group_name:
            return obj['id']
    return None

# Helper function to get tactics, techniques, procedures for a given intrusion-set ID
def get_related_ttps(intrusion_set_id, attack_objects):
    techniques = []
    tools = []

    for obj in attack_objects:
        if obj['type'] == 'relationship' and obj.get('source_ref') == intrusion_set_id:
            target_ref = obj.get('target_ref')
            target_obj = next((item for item in attack_objects if item['id'] == target_ref), None)
            if target_obj:
                if target_obj['type'] == 'attack-pattern':
                    technique_info = {
                        "Technique ID": target_obj['external_references'][0].get('external_id', 'N/A'),
                        "Technique Name": target_obj.get('name', 'N/A'),
                        "Description": target_obj.get('description', 'N/A'),
                        "Tactic": target_obj.get('kill_chain_phases', [{'phase_name': 'N/A'}])[0].get('phase_name', 'N/A')
                    }
                    techniques.append(technique_info)
                elif target_obj['type'] == 'tool':
                    tool_info = {
                        "Tool ID": target_obj['external_references'][0].get('external_id', 'N/A'),
                        "Tool Name": target_obj.get('name', 'N/A'),
                        "Description": target_obj.get('description', 'N/A')
                    }
                    tools.append(tool_info)
                    
    return techniques, tools

# Load the data and process it again with the helper functions
with open('../data/enterprise-attack.json') as f:
    enterprise_attack = json.load(f)

# Get FIN7 intrusion-set ID
fin7_id = get_intrusion_set_id("FIN7", enterprise_attack['objects'])

# Get TTPs and tools related to FIN7
fin7_techniques, fin7_tools = get_related_ttps(fin7_id, enterprise_attack['objects'])

# Convert lists to DataFrames for display
fin7_techniques_df = pd.DataFrame(fin7_techniques)
fin7_tools_df = pd.DataFrame(fin7_tools)

# Display techniques
fin7_techniques_df.head() # Display the first few rows to ensure correctness

Technique ID                     Technique Name  \
0    T1204.001                     Malicious Link   
1    T1553.002                       Code Signing   
2        T1078                     Valid Accounts   
3        T1059  Command and Scripting Interpreter   
4    T1021.004                                SSH   

                                         Description            Tactic  
0  An adversary may rely upon a user clicking a m...         execution  
1  Adversaries may create, acquire, or steal code...   defense-evasion  
2  Adversaries may obtain and abuse credentials o...   defense-evasion  
3  Adversaries may abuse command and script inter...         execution  
4  Adversaries may use [Valid Accounts](https://a...  lateral-movement

In [9]:
#Display tools
fin7_tools_df.head() # Display the first few rows to ensure correctness

Tool ID     Tool Name                                        Description
0   S0002      Mimikatz  [Mimikatz](https://attack.mitre.org/software/S...
1   S0552        AdFind  [AdFind](https://attack.mitre.org/software/S05...
2   S0194   PowerSploit  [PowerSploit](https://attack.mitre.org/softwar...
3   S0488  CrackMapExec  [CrackMapExec](https://attack.mitre.org/softwa...

In [10]:
############################################################

In [11]:
# Trying a simpler approach due to repeated internal errors

# Search for techniques and tools directly within the attack objects that mention being used by FIN7
fin7_techniques = []
fin7_tools = []

intrusion_set_refs = [
    obj['id'] for obj in enterprise_attack['objects'] 
    if obj['type'] == 'intrusion-set' and obj.get('name') == 'FIN7'
]

if intrusion_set_refs:
    fin7_id = intrusion_set_refs[0]
    
    for obj in enterprise_attack['objects']:
        if 'description' in obj and 'FIN7' in obj['description']:
            if obj['type'] == 'attack-pattern':
                fin7_techniques.append({
                    "Technique ID": obj['external_references'][0].get('external_id', 'N/A'),
                    "Technique Name": obj.get('name', 'N/A'),
                    "Description": obj.get('description', 'N/A'),
                    "Tactic": obj.get('kill_chain_phases', [{'phase_name': 'N/A'}])[0].get('phase_name', 'N/A')
                })
            elif obj['type'] == 'tool':
                fin7_tools.append({
                    "Tool ID": obj['external_references'][0].get('external_id', 'N/A'),
                    "Tool Name": obj.get('name', 'N/A'),
                    "Description": obj.get('description', 'N/A')
                })

# Convert lists to DataFrames for display
fin7_techniques_df = pd.DataFrame(fin7_techniques)
fin7_tools_df = pd.DataFrame(fin7_tools)

# Display the dataframes
fin7_techniques_df.head()#, fin7_tools_df.head()

Technique ID              Technique Name  \
0    T1587.001                     Malware   
1    T1218.005                       Mshta   
2    T1497.002  User Activity Based Checks   
3        T1170                       Mshta   

                                         Description                Tactic  
0  Adversaries may develop malware and malware co...  resource-development  
1  Adversaries may abuse mshta.exe to proxy execu...       defense-evasion  
2  Adversaries may employ various user activity c...       defense-evasion  
3  Mshta.exe is a utility that executes Microsoft...       defense-evasion

In [12]:
############################################################

In [13]:
# Manually extracting first few references from the dataset to avoid internal exceptions

# List to store manually extracted techniques and tools for FIN7
manual_fin7_techniques = [
    {
        "Technique ID": "T1027",
        "Technique Name": "Obfuscated Files or Information",
        "Description": "FIN7 has used services such as [pastebin.com](https://pastebin.com) for obfuscating encoded PowerShell commands.",
        "Tactic": "Defense Evasion"
    },
    {
        "Technique ID": "T1105",
        "Technique Name": "Ingress Tool Transfer",
        "Description": "FIN7 has downloaded PowerShell and VBScript onto victim machines.",
        "Tactic": "Command and Control"
    }
]

manual_fin7_tools = [
    {
        "Tool ID": "S0496",
        "Tool Name": "HALFBAKED",
        "Description": "HALFBAKED is a downloader used by FIN7 for further payload delivery."
    },
    {
        "Tool ID": "S0466",
        "Tool Name": "TIRION",
        "Description": "TIRION is a PowerShell backdoor used by FIN7 for network reconnaissance."
    }
]

# Convert lists to DataFrames for display
manual_fin7_techniques_df = pd.DataFrame(manual_fin7_techniques)
manual_fin7_tools_df = pd.DataFrame(manual_fin7_tools)

# Display the dataframes
manual_fin7_techniques_df.head()

Technique ID                   Technique Name  \
0        T1027  Obfuscated Files or Information   
1        T1105            Ingress Tool Transfer   

                                         Description               Tactic  
0  FIN7 has used services such as [pastebin.com](...      Defense Evasion  
1  FIN7 has downloaded PowerShell and VBScript on...  Command and Control

In [14]:
manual_fin7_tools_df.head()

Tool ID  Tool Name                                        Description
0   S0496  HALFBAKED  HALFBAKED is a downloader used by FIN7 for fur...
1   S0466     TIRION  TIRION is a PowerShell backdoor used by FIN7 f...

In [15]:
############################################################

In [16]:
# Load the NIST SP 800-53 controls mapping to MITRE ATT&CK techniques
with open('../data/nist_800_53-rev5_attack-14.1-enterprise_json.json') as f:
    nist_mapping = json.load(f)

In [17]:
print(nist_mapping)

# print_obj = nist_mapping
# pretty_json = json.dumps(print_obj, indent=4)
# print(pretty_json)

print(json.dumps(nist_mapping, indent=4))

{'metadata': {'mapping_version': '', 'technology_domain': 'enterprise', 'attack_version': '14.1', 'mapping_framework': 'nist_800_53', 'mapping_framework_version': 'rev5', 'author': None, 'contact': None, 'organization': None, 'creation_date': '01/13/2022', 'last_update': '01/13/2022', 'mapping_types': {'protects': {'name': 'Protects', 'description': ''}, 'non_mappable': {'name': 'Non-Mappable', 'description': ''}}, 'capability_groups': {'AC': 'Access Control', 'CA': 'Security Assessment and Authorization', 'CM': 'Configuration Management', 'SC': 'System and Communications Protection', 'SI': 'System and Information Integrity', 'CP': 'Contingency Planning', 'IA': 'Identification and Authentication', 'SA': 'System and Services Acquisition', 'RA': 'Risk Assessment', 'MP': 'Media Protection', 'SR': 'Supply Chain Risk Management'}}, 'mapping_objects': [{'capability_id': None, 'capability_group': None, 'capability_description': None, 'attack_object_id': 'T1608.006', 'attack_object_name': 'SEO

In [18]:
print(nist_mapping.keys())

dict_keys(['metadata', 'mapping_objects'])


In [19]:
#print(nist_mapping['mapping_objects'][:5])

# print_obj = nist_mapping['mapping_objects'][:5]
# pretty_json = json.dumps(print_obj, indent=4)
# print(pretty_json)

print(json.dumps(nist_mapping['mapping_objects'][:5], indent=4))

[
    {
        "capability_id": null,
        "capability_group": null,
        "capability_description": null,
        "attack_object_id": "T1608.006",
        "attack_object_name": "SEO Poisoning",
        "references": [],
        "mapping_type": "non_mappable"
    },
    {
        "capability_id": null,
        "capability_group": null,
        "capability_description": null,
        "attack_object_id": "T1608.005",
        "attack_object_name": "Link Target",
        "references": [],
        "mapping_type": "non_mappable"
    },
    {
        "capability_id": null,
        "capability_group": null,
        "capability_description": null,
        "attack_object_id": "T1608.004",
        "attack_object_name": "Drive-by Target",
        "references": [],
        "mapping_type": "non_mappable"
    },
    {
        "capability_id": null,
        "capability_group": null,
        "capability_description": null,
        "attack_object_id": "T1608.003",
        "attack_object_name": "In

In [20]:
def extract_relevant_nist_controls(technique_ids, nist_mapping):
    nist_controls = []
    
    for obj in nist_mapping["mapping_objects"]:
        if obj["attack_object_id"] in technique_ids:
            nist_controls.append({
                "attack_object_id": obj["attack_object_id"],
                "attack_object_name": obj["attack_object_name"],
                "mapping_type": obj["mapping_type"],
                "capability_id": obj["capability_id"],
                "capability_group": obj["capability_group"],
                "capability_description": obj["capability_description"]
            })
    
    return nist_controls

# List of MITRE technique IDs
technique_ids = ["T1204.001", "T1553.002", "T1078", "T1059", "T1021.004"]

# Extract relevant NIST controls
relevant_nist_controls = extract_relevant_nist_controls(technique_ids, nist_mapping)

# Print the extracted NIST controls
print(json.dumps(relevant_nist_controls, indent=4))

[
    {
        "attack_object_id": "T1021.004",
        "attack_object_name": "SSH",
        "mapping_type": "protects",
        "capability_id": "AC-17",
        "capability_group": "AC",
        "capability_description": "Remote Access"
    },
    {
        "attack_object_id": "T1021.004",
        "attack_object_name": "SSH",
        "mapping_type": "protects",
        "capability_id": "AC-02",
        "capability_group": "AC",
        "capability_description": "Account Management"
    },
    {
        "attack_object_id": "T1021.004",
        "attack_object_name": "SSH",
        "mapping_type": "protects",
        "capability_id": "AC-20",
        "capability_group": "AC",
        "capability_description": "Use of External Systems"
    },
    {
        "attack_object_id": "T1021.004",
        "attack_object_name": "SSH",
        "mapping_type": "protects",
        "capability_id": "AC-03",
        "capability_group": "AC",
        "capability_description": "Access Enforcement"
    }

In [21]:
relevant_nist_controls_df = pd.DataFrame(relevant_nist_controls)
relevant_nist_controls_df

attack_object_id attack_object_name mapping_type capability_id  \
0         T1021.004                SSH     protects         AC-17   
1         T1021.004                SSH     protects         AC-02   
2         T1021.004                SSH     protects         AC-20   
3         T1021.004                SSH     protects         AC-03   
4         T1021.004                SSH     protects         AC-05   
..              ...                ...          ...           ...   
70            T1078     Valid Accounts     protects         SA-04   
71            T1078     Valid Accounts     protects         SA-08   
72            T1078     Valid Accounts     protects         SC-28   
73            T1078     Valid Accounts     protects         SI-04   
74            T1078     Valid Accounts     protects         SR-06   

   capability_group                       capability_description  
0                AC                                Remote Access  
1                AC                           Account Management  
2                AC                      Use of External Systems  
3                AC                           Access Enforcement  
4                AC                         Separation of Duties  
..              ...                                          ...  
70               SA                          Acquisition Process  
71               SA  Security and Privacy Engineering Principles  
72               SC            Protection of Information at Rest  
73               SI                            System Monitoring  
74               SR             Supplier Assessments and Reviews  

[75 rows x 6 columns]

In [41]:
# Load the NIST SP 800-53 controls mapping to MITRE ATT&CK techniques
with open('../data/nist_800_53-rev5_attack-14.1-enterprise_json.json') as f:
    nist_mapping = json.load(f)

In [42]:
# Print the extracted NIST controls
print(json.dumps(nist_mapping, indent=4))

{
    "metadata": {
        "mapping_version": "",
        "technology_domain": "enterprise",
        "attack_version": "14.1",
        "mapping_framework": "nist_800_53",
        "mapping_framework_version": "rev5",
        "author": null,
        "contact": null,
        "organization": null,
        "creation_date": "01/13/2022",
        "last_update": "01/13/2022",
        "mapping_types": {
            "protects": {
                "name": "Protects",
                "description": ""
            },
            "non_mappable": {
                "name": "Non-Mappable",
                "description": ""
            }
        },
        "capability_groups": {
            "AC": "Access Control",
            "CA": "Security Assessment and Authorization",
            "CM": "Configuration Management",
            "SC": "System and Communications Protection",
            "SI": "System and Information Integrity",
            "CP": "Contingency Planning",
            "IA": "Identification a

In [46]:
# Function to extract relevant NIST controls for the given MITRE technique IDs
def get_nist_controls(technique_ids, nist_mapping):
    controls_mapping = []
    if 'mapping_objects' not in nist_mapping:
        print("Key 'mapping_objects' not found in nist_mapping")
        return controls_mapping
    
    for control in nist_mapping['mapping_objects']:
        if 'mapping_type' in control and control['mapping_type'] == 'protects':
            attack_object_id = control.get('attack_object_id')
            attack_object_name = control.get('attack_object_name')
            capability_id = control.get('capability_id')
            capability_description = control.get('capability_description')
            if attack_object_id in technique_ids:
                controls_mapping.append({
                    'technique_id': attack_object_id,
                    'technique_name': attack_object_name,
                    'nist_control': capability_id,
                    'nist_control_description': capability_description
                })
    
    return controls_mapping    
    
    # for control in nist_mapping['mapping_objects']:
    #     if control['mapping_type'] == 'protects':
    #         source_ref = control.get('source_ref')
    #         target_ref = control.get('target_ref')
    #         target_obj = next((item for item in nist_mapping['mapping_objects'] if item['id'] == target_ref), None)
    #         if target_obj and target_obj['external_references'][0]['external_id'] in technique_ids:
    #             source_obj = next((item for item in nist_mapping['mapping_objects'] if item['id'] == source_ref), None)
    #             if source_obj:
    #                 controls_mapping.append({
    #                     "Technique ID": target_obj['external_references'][0]['external_id'],
    #                     "Control ID": source_obj['external_references'][0]['external_id'],
    #                     "Control Description": source_obj.get('description', 'N/A')
    #                 })
    # return controls_mapping

# Define the MITRE Technique IDs to map
technique_ids = ["T1204.001", "T1553.002", "T1078", "T1059", "T1021.004"]

# Get the relevant NIST controls for the given MITRE Technique IDs
nist_controls = get_nist_controls(technique_ids, nist_mapping)

# Convert to DataFrame for display purposes
nist_controls_df = pd.DataFrame(nist_controls)
nist_controls_df.head()  # Display the first few rows to ensure correct mapping

technique_id technique_name nist_control nist_control_description
0    T1021.004            SSH        AC-17            Remote Access
1    T1021.004            SSH        AC-02       Account Management
2    T1021.004            SSH        AC-20  Use of External Systems
3    T1021.004            SSH        AC-03       Access Enforcement
4    T1021.004            SSH        AC-05     Separation of Duties

In [47]:
nist_controls_df

technique_id  technique_name nist_control  \
0     T1021.004             SSH        AC-17   
1     T1021.004             SSH        AC-02   
2     T1021.004             SSH        AC-20   
3     T1021.004             SSH        AC-03   
4     T1021.004             SSH        AC-05   
..          ...             ...          ...   
70        T1078  Valid Accounts        SA-04   
71        T1078  Valid Accounts        SA-08   
72        T1078  Valid Accounts        SC-28   
73        T1078  Valid Accounts        SI-04   
74        T1078  Valid Accounts        SR-06   

                       nist_control_description  
0                                 Remote Access  
1                            Account Management  
2                       Use of External Systems  
3                            Access Enforcement  
4                          Separation of Duties  
..                                          ...  
70                          Acquisition Process  
71  Security and Privacy Engineering Principles  
72            Protection of Information at Rest  
73                            System Monitoring  
74             Supplier Assessments and Reviews  

[75 rows x 4 columns]

In [ ]:
##########################################

In [23]:
# Trying a simpler approach to avoid internal exceptions

# Manually map a few NIST controls from the NIST 800-53 publication related to given MITRE techniques

# List to store manual mappings
manual_nist_controls = [
    {
        "Technique ID": "T1204.001",
        "Control ID": "SI-4",
        "Control Description": "Information System Monitoring - Monitor the information system to detect attacks and indicators of potential attacks."
    },
    {
        "Technique ID": "T1204.001",
        "Control ID": "CA-7",
        "Control Description": "Continuous Monitoring - Establish a continuous monitoring strategy and implement a continuous monitoring program."
    },
    {
        "Technique ID": "T1553.002",
        "Control ID": "IA-2",
        "Control Description": "Identification and Authentication (Organizational Users) - Ensure that individuals accessing the system are authorized."
    },
    {
        "Technique ID": "T1553.002",
        "Control ID": "AC-17",
        "Control Description": "Remote Access - Establish and manage remote access to the system."
    },
    {
        "Technique ID": "T1078",
        "Control ID": "IA-4",
        "Control Description": "Identifier Management - Manage information system identifiers for individuals requiring access."
    },
    {
        "Technique ID": "T1059",
        "Control ID": "SI-3",
        "Control Description": "Malicious Code Protection - Implement anti-malware protection capabilities at system entry and exit points."
    },
    {
        "Technique ID": "T1021.004",
        "Control ID": "AC-3",
        "Control Description": "Access Enforcement - Enforce approved authorizations for logical access to the system."
    }
]

# Convert to DataFrame for display
manual_nist_controls_df = pd.DataFrame(manual_nist_controls)

# Display the DataFrame
manual_nist_controls_df

Technique ID Control ID                                Control Description
0    T1204.001       SI-4  Information System Monitoring - Monitor the in...
1    T1204.001       CA-7  Continuous Monitoring - Establish a continuous...
2    T1553.002       IA-2  Identification and Authentication (Organizatio...
3    T1553.002      AC-17  Remote Access - Establish and manage remote ac...
4        T1078       IA-4  Identifier Management - Manage information sys...
5        T1059       SI-3  Malicious Code Protection - Implement anti-mal...
6    T1021.004       AC-3  Access Enforcement - Enforce approved authoriz...